In [49]:
import requests 
import pandas as pd  
r = requests.get('https://www.politifact.com/truth-o-meter/statements/')
from bs4 import BeautifulSoup  
from pymongo import MongoClient
import json


In [50]:
def insert_data(data):
     
    MONGO_URL = "mongodb://newsdata:ZG4cTh2XbyUpkiVggEcQ6lL6UEC32iJThy4eZrO9RLY1suKiXdUNrqi5pzrqzqNvUsdO9xAxjhyFfNfNVoBeXA==@newsdata.documents.azure.com:10255/?ssl=true&replicaSet=globaldb"
    client = MongoClient(MONGO_URL)
    db = client.fakenewsdb
               # Decode the JSON from Twitter
        #datajson = json.loads(data)
    db.politico_facts_data.update({"Statement_url":data[0]['Statement_url']},data[0],upsert=True)
       
    

In [51]:
soup = BeautifulSoup(r.text, 'html.parser')  
results = soup.find_all('div', attrs={'class':'scoretable__item'})
#print(len(results))

records = []  
for result in results:  
    date = result.find('span',attrs={'class':'article__meta'}).text
    statement_source = result.find('div',attrs={'class':'statement__source'}).text
    statement =  result.find('a', attrs={'class':'link'}).text
    statement_url = result.find('a', attrs={'class':'link'})['href']
    fact = result.find('p', attrs={'class':'quote'}).text
    url =  result.find('a')['href'] 
    meter = result.find('div',attrs={'class':'meter'}).find('img',alt=True)['alt']
    records.append(( date,meter,statement_source,statement,statement_url,fact, url))
    insert_data([{"Date":date,"Meter":meter,"Source":statement_source,"Statement":statement,"Statement_url":statement_url,"Fact":fact,"Source_Url":url}])



paginationDetails = soup.find('div', attrs={'class':'pagination'}).find('span',attrs={'class':'step-links__current'}).text
paginationDetails = paginationDetails.rstrip().lstrip().split()
pagecount = int(paginationDetails[len(paginationDetails)-1])
pagecount

C:\Users\chami\Anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: update is deprecated. Use replace_one, update_one or update_many instead.
  


778

In [52]:
for i in range(2,pagecount):
    r = requests.get('https://www.politifact.com/truth-o-meter/statements/?page='+str(i))
    soup = BeautifulSoup(r.text, 'html.parser')  
    results = soup.find_all('div', attrs={'class':'scoretable__item'})
#print(len(results))


    for result in results:  
        date = result.find('span',attrs={'class':'article__meta'}).text
        statement_source = result.find('div',attrs={'class':'statement__source'}).text
        statement =  result.find('a', attrs={'class':'link'}).text
        statement_url = result.find('a', attrs={'class':'link'})['href']
        fact = result.find('p', attrs={'class':'quote'}).text
        url =  result.find('a')['href'] 
        meter = result.find('div',attrs={'class':'meter'}).find('img',alt=True)['alt']
        
        records.append(( date,meter,statement_source,statement,statement_url,fact, url))
        insert_data([{"Date":date,"Meter":meter,"Source":statement_source,"Statement":statement,"Statement_url":statement_url,"Fact":fact,"Source_Url":url}])



C:\Users\chami\Anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: update is deprecated. Use replace_one, update_one or update_many instead.
  


In [53]:
df = pd.DataFrame(records, columns=['Date','Meter', 'Source','Statement','Statment_url','Fact', 'Source_Url'])  
df

Date           Meter  \
0         on Sunday, December 23rd, 2018       Half-True   
1         on Friday, December 21st, 2018     Mostly True   
2         on Friday, December 21st, 2018           False   
3       on Thursday, December 20th, 2018  Pants on Fire!   
4       on Thursday, December 20th, 2018  Pants on Fire!   
5       on Thursday, December 20th, 2018       Half-True   
6       on Thursday, December 20th, 2018           False   
7      on Wednesday, December 19th, 2018           False   
8      on Wednesday, December 19th, 2018  Pants on Fire!   
9      on Wednesday, December 19th, 2018       Half-True   
10     on Wednesday, December 19th, 2018  Pants on Fire!   
11     on Wednesday, December 19th, 2018  Pants on Fire!   
12       on Tuesday, December 18th, 2018  Pants on Fire!   
13       on Tuesday, December 18th, 2018     Mostly True   
14       on Tuesday, December 18th, 2018           False   
15       on Tuesday, December 18th, 2018    Mostly False   
16       on Tuesday, December 18th, 2018  Pants on Fire!   
17       on Tuesday, December 18th, 2018           False   
18       on Tuesday, December 18th, 2018         No Flip   
19        on Sunday, December 16th, 2018       Half-True   
20        on Friday, December 14th, 2018     Mostly True   
21        on Friday, December 14th, 2018     Mostly True   
22        on Friday, December 14th, 2018       Half-True   
23      on Thursday, December 13th, 2018  Pants on Fire!   
24      on Thursday, December 13th, 2018           False   
25      on Thursday, December 13th, 2018     Mostly True   
26      on Thursday, December 13th, 2018     Mostly True   
27      on Thursday, December 13th, 2018            True   
28     on Wednesday, December 12th, 2018       Half-True   
29     on Wednesday, December 12th, 2018            True   
...                                  ...             ...   
15510     on Monday, September 3rd, 2007            True   
15511   on Saturday, September 1st, 2007           False   
15512   on Saturday, September 1st, 2007     Mostly True   
15513     on Thursday, August 30th, 2007    Mostly False   
15514     on Thursday, August 30th, 2007     Mostly True   
15515     on Thursday, August 30th, 2007  Pants on Fire!   
15516     on Thursday, August 30th, 2007     Mostly True   
15517    on Wednesday, August 29th, 2007       Half-True   
15518      on Tuesday, August 28th, 2007     Mostly True   
15519       on Monday, August 27th, 2007            True   
15520       on Friday, August 24th, 2007  Pants on Fire!   
15521     on Thursday, August 23rd, 2007       Half-True   
15522     on Thursday, August 23rd, 2007     Mostly True   
15523     on Thursday, August 23rd, 2007     Mostly True   
15524    on Wednesday, August 22nd, 2007       Half-True   
15525    on Wednesday, August 22nd, 2007       Half-True   
15526      on Tuesday, August 21st, 2007            True   
15527      on Tuesday, August 21st, 2007       Half-True   
15528      on Tuesday, August 21st, 2007       Half-True   
15529       on Monday, August 20th, 2007     Mostly True   
15530       on Friday, August 10th, 2007       Half-True   
15531       on Tuesday, August 7th, 2007           False   
15532        on Monday, August 6th, 2007       Half-True   
15533     on Wednesday, August 1st, 2007            True   
15534     on Wednesday, August 1st, 2007     Mostly True   
15535        on Tuesday, July 10th, 2007            True   
15536         on Friday, June 22nd, 2007       Half-True   
15537       on Thursday, June 21st, 2007       Half-True   
15538        on Tuesday, June 19th, 2007     Mostly True   
15539        on Tuesday, June 12th, 2007           False   

                               Source  \
0                      Garry McCarthy   
1                    Dallas Woodhouse   
2                        Donald Trump   
3                            Bloggers   
4                            Bloggers   
5                            Bloggers   
6                           

In [54]:
df.index +=1
df.reset_index()
df["id"] = df.index

In [55]:
cols = df.columns.tolist()
cols = cols[-1:] + cols[:-1]
df=df[cols]
json = df.to_json(orient="records")

In [56]:
json

'[{"id":1,"Date":"on Sunday, December 23rd, 2018","Meter":"Half-True","Source":"Garry McCarthy","Statement":"\\"There was almost a 70 percent reduction in police-related shootings under my tenure because of training, supervision and policy decisions.\\"\\r\\n","Statment_url":"\\/illinois\\/statements\\/2018\\/dec\\/23\\/garry-mccarthy\\/did-police-shootings-plunge-under-mccarthys-leader\\/","Fact":"The numbers fell, but that doesn\'t mean he can take all the credit","Source_Url":"\\/personalities\\/garry-mccarthy\\/statements\\/byruling\\/half-true\\/"},{"id":2,"Date":"on Friday, December 21st, 2018","Meter":"Mostly True","Source":"Dallas Woodhouse","Statement":"Says no elections protest was filed, McCready conceded and \\"every\\" county board certified its results from the Mark Harris, Dan McCready race.\\r\\n","Statment_url":"\\/north-carolina\\/statements\\/2018\\/dec\\/21\\/dallas-woodhouse\\/nc-gop-leader-mostly-right-about-lack-protests-ele\\/","Fact":"But the claims don\'t nece

In [57]:
df.to_csv("politico_records.csv", sep='\t')